In [1]:
import findspark
findspark.init()
findspark.find()
import pyspark
from pyspark.sql import SparkSession
import pyspark.sql.functions as f

from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.context import SparkContext
from pyspark.sql.session import SparkSession
from pyspark.ml.feature import Tokenizer
from pyspark.ml.feature import StopWordsRemover
from pyspark.sql.functions import col,from_json
from pyspark.sql.types import StructType,StructField, StringType
spark = SparkSession.builder \
    .master('local[*]') \
    .config("spark.driver.memory", "15g") \
    .config("spark.driver.maxResultSize", "5g")\
    .config('spark.executor.instances', 4)\
    .config('spark.executor.cores', 4)\
    .config('spark.executor.memory', '10g')\
    .config('spark.driver.memory', '15g')\
    .config('spark.memory.offHeap.enabled', True)\
    .config('spark.memory.offHeap.size', '20g')\
    .appName('twitter-data') \
    .getOrCreate()
sc = spark.sparkContext

In [2]:
#inp= sc.textFile("twitter_small.txt",10).map(lambda x: x.split(', '))
#inp.getNumPartitions()

#print(inp.getNumPartitions())
txt = sc.textFile("twitter_small.txt",10).map(lambda x: x.split('": '))

#remove header
txt.collect()

[['{"created_at',
  '"Fri May 29 15:38:52 +0000 2020", "id',
  '1266393580223987713, "id_str',
  '"1266393580223987713", "full_text',
  '"RT @Desiree_Laverne: #MyBeautifulAfrica....\\u2764\\nAardwolf.. https://t.co/9C7MjkQaIp", "truncated',
  'false, "display_text_range',
  '[0, 79], "entities',
  '{"hashtags',
  '[{"text',
  '"MyBeautifulAfrica", "indices',
  '[21, 39]}], "symbols',
  '[], "user_mentions',
  '[{"screen_name',
  '"Desiree_Laverne", "name',
  '"Desiree_Laverne", "id',
  '2314937901, "id_str',
  '"2314937901", "indices',
  '[3, 19]}], "urls',
  '[], "media',
  '[{"id',
  '1266286817315176450, "id_str',
  '"1266286817315176450", "indices',
  '[56, 79], "media_url',
  '"http://pbs.twimg.com/media/EZLBJrnUwAI9IbT.jpg", "media_url_https',
  '"https://pbs.twimg.com/media/EZLBJrnUwAI9IbT.jpg", "url',
  '"https://t.co/9C7MjkQaIp", "display_url',
  '"pic.twitter.com/9C7MjkQaIp", "expanded_url',
  '"https://twitter.com/Desiree_Laverne/status/1266286830116200448/photo/1", "type',


In [3]:
txt.collect()[0][1]


'"Fri May 29 15:38:52 +0000 2020", "id'

In [4]:
txt.collect()[1][4]

'"@wovenwn @GSBdestek Eveet", "truncated'

In [5]:
txt.collect()[0][4]

'"RT @Desiree_Laverne: #MyBeautifulAfrica....\\u2764\\nAardwolf.. https://t.co/9C7MjkQaIp", "truncated'

In [6]:
rdd=txt.map(lambda x: (x[1], x[4])).distinct()
for element in rdd.collect():
    print(element)

('"Fri May 29 15:38:51 +0000 2020", "id', '"@SintSonja @PolitiekDelftnl @Avalex_nieuws @Mar10aH @Zuidpoort @jpdewit @gjevalk @KoelewijnMarcel Als ik een melding maak via de buitenbeter app wordt het de volgende opgehaald", "truncated')
('"Fri May 29 15:38:51 +0000 2020", "id', '"RT @narkobars: Shoegaze\\n\\nhttps://t.co/Rs0yxl0hA8", "truncated')
('"Fri May 29 15:38:50 +0000 2020", "id', '"@KellyOverCorona Posturaal Orthostatisch Tachycardia Syndroom. Hartslag gaat sterk omhoog bij het rechtop zijn. Trappen af gaat nog, maar omhoog te zwaar. \\n\\nIk las idd net dat honderdduizenden in quarantaine zijn, onnodig met containment.", "truncated')
('"Fri May 29 15:38:48 +0000 2020", "id', '"@Tobientin Jajasjjsjaaassss\\ud83d\\ude0e\\ud83d\\ude0e", "truncated')
('"Fri May 29 15:38:48 +0000 2020", "id', '"@Timm025 Open dm", "truncated')
('"Fri May 29 15:38:47 +0000 2020", "id', '"@Nieuwsblad_be Dit is pas kwalitatieve journalistiek nu ben ik echt wel aan het overwegen om een abonnement aan te 

('"Fri May 29 15:27:33 +0000 2020", "id', '"@Crewchi56565307 @GVB_klanten Nee, toen mocht ik niet zwartrijden van mijn moeder.\\nNog steeds niet trouwens.", "truncated')
('"Fri May 29 15:27:33 +0000 2020", "id', '"Maam. https://t.co/Iu7jAB4lLE", "truncated')
('"Fri May 29 15:27:33 +0000 2020", "id', '"@drakoridfess a-teen 1&amp;2", "truncated')
('"Fri May 29 15:27:31 +0000 2020", "id', '"RT @Matthijs85: WHO en RIVM baseren zich nog steeds op kennis uit de jaren \'30.. \\ud83e\\udd28 #corona #COVID19\\n\\nSinds we de technische mogelijkheid he\\u2026", "truncated')
('"Fri May 29 15:27:30 +0000 2020", "id', '"#Woensdrecht - Met 260 kilometer per uur achter verdachten van witwassen aan op A58 bij Roosendaal https://t.co/IwLBTGPSHV", "truncated')
('"Fri May 29 15:27:29 +0000 2020", "id', '"RT @cdavandaag: Wil jij d\\u00e9 1 juno mok van @ferdgrapperhaus? De tien hoogste bieders krijgen hem thuisgestuurd! De opbrengst gaat voor 100%\\u2026", "truncated')
('"Fri May 29 15:27:27 +0000 2020", 

('"Fri May 29 15:34:10 +0000 2020", "id', '"@SusanWa27778239 eweofwo regkerpg okerokgorkger lokodkd dvkjdvj\\u0131dvs dso ojw\\u0131fjwgrrw", "truncated')
('"Fri May 29 15:34:10 +0000 2020", "id', '"@HassanI53459131 @ninashninash2g1 @M_3angels @snowye29 7aram 3leyk, Chou cheft ? Kam we7de \\ud83d\\ude02", "truncated')
('"Fri May 29 15:34:10 +0000 2020", "id', '"RT @janpaulvansoest: Trouw bespreekt waarom de resultaten van 30 jaar natuurbeleid zo mager zijn (@trouw gisteren). Mijn beeld: we proberen\\u2026", "truncated')
('"Fri May 29 15:34:09 +0000 2020", "id', '"@KelRebel Als ik de buurvrouw was, dan had ik niks gezegd en gedacht \\"oeh la la\\"", "truncated')
('"Fri May 29 15:34:09 +0000 2020", "id', '"IJWMDS", "truncated')
('"Fri May 29 15:34:07 +0000 2020", "id', '"@chamyhoney_ Charlie babyboy wjsiksnskskw", "truncated')
('"Fri May 29 15:34:06 +0000 2020", "id', '"RT @RenskeLeijten: Het oorspronkelijke geschatte bedrag - door \\u201cu vraagt wij draaien\\u201d consultants - aan bel

('"Fri May 29 15:36:03 +0000 2020", "id', '"RT @ReneDercksen: Asielzoekerscentrum te Burgum.\\n\\nKunt u een grotere middelvinger naar hard werkend en woningzoekend Nederland voorstellen?\\u2026", "truncated')
('"Fri May 29 15:36:02 +0000 2020", "id', '"\\u201cHet is tijd dat gamers van de features van PS5 kunnen genieten\\u201d\\n\\nhttps://t.co/Ng5GykdJxw", "truncated')
('"Fri May 29 15:36:02 +0000 2020", "id', '"RT @bdossenomgeving: Drie gewonden bij vermoedelijke explosie bij oliehandel in Lithooijen https://t.co/s06MOOZTip", "truncated')
('"Fri May 29 15:36:01 +0000 2020", "id', '"Word door de \\"consumentenberg\\" gebeld: \\"ik zie dat u nog niet mee gegaan ben met de daling in gas en licht prijzen\\"\\n\\nHoe ziet u dat? 3x herhaald geen antwoord en zij hangt op....\\n\\n+31302040727 kan niet teruggebeld worden. Vaag vaag vaag.", "truncated')
('"Fri May 29 15:35:57 +0000 2020", "id', '"@WendySteen Zie, kan de beste overkomen", "truncated')
('"Fri May 29 15:35:55 +0000 2020", "id

In [7]:
rdd.collect()

[('"Fri May 29 15:38:51 +0000 2020", "id',
  '"@SintSonja @PolitiekDelftnl @Avalex_nieuws @Mar10aH @Zuidpoort @jpdewit @gjevalk @KoelewijnMarcel Als ik een melding maak via de buitenbeter app wordt het de volgende opgehaald", "truncated'),
 ('"Fri May 29 15:38:51 +0000 2020", "id',
  '"RT @narkobars: Shoegaze\\n\\nhttps://t.co/Rs0yxl0hA8", "truncated'),
 ('"Fri May 29 15:38:50 +0000 2020", "id',
  '"@KellyOverCorona Posturaal Orthostatisch Tachycardia Syndroom. Hartslag gaat sterk omhoog bij het rechtop zijn. Trappen af gaat nog, maar omhoog te zwaar. \\n\\nIk las idd net dat honderdduizenden in quarantaine zijn, onnodig met containment.", "truncated'),
 ('"Fri May 29 15:38:48 +0000 2020", "id',
  '"@Tobientin Jajasjjsjaaassss\\ud83d\\ude0e\\ud83d\\ude0e", "truncated'),
 ('"Fri May 29 15:38:48 +0000 2020", "id', '"@Timm025 Open dm", "truncated'),
 ('"Fri May 29 15:38:47 +0000 2020", "id',
  '"@Nieuwsblad_be Dit is pas kwalitatieve journalistiek nu ben ik echt wel aan het overwegen om e

In [8]:
deptSchema = StructType([       
    StructField('Date', StringType(), True),
    StructField('Text', StringType(), True)
])

In [9]:
DF1 = spark.createDataFrame(rdd, schema = deptSchema)



In [10]:
DF1.show()


+--------------------+--------------------+
|                Date|                Text|
+--------------------+--------------------+
|"Fri May 29 15:38...|"@SintSonja @Poli...|
|"Fri May 29 15:38...|"RT @narkobars: S...|
|"Fri May 29 15:38...|"@KellyOverCorona...|
|"Fri May 29 15:38...|"@Tobientin Jajas...|
|"Fri May 29 15:38...|"@Timm025 Open dm...|
|"Fri May 29 15:38...|"@Nieuwsblad_be D...|
|"Fri May 29 15:38...|"@OzanKemalOzan @...|
|"Fri May 29 15:38...|"@SQ__D @TorfsBot...|
|"Fri May 29 15:38...|"\ud83c\udfac Maa...|
|"Fri May 29 15:38...|"@ciciloqq hy wel...|
|"Fri May 29 15:38...|"Hercule Poirot  ...|
|"Fri May 29 15:38...|"@gbr8898 @MattHD...|
|"Fri May 29 15:38...|"@FransOldejans A...|
|"Fri May 29 15:38...|"@crypto4all9 @NO...|
|"Fri May 29 15:38...|"jungkook wtf kdj...|
|"Fri May 29 15:38...|"RT @STUDIOdebali...|
|"Fri May 29 15:38...|"like w htklem 3n...|
|"Fri May 29 15:38...|"Andre Rieu Amazi...|
|"Fri May 29 15:38...|"@AdvocaatBoone I...|
|"Fri May 29 15:38...|"@victoria

In [11]:
tokenizer2 = Tokenizer(inputCol="Text", outputCol="words_token")
tokenized = tokenizer2.transform(DF1).select('Date','Text','words_token')
remover = StopWordsRemover(stopWords=["aan","af","al","als","bij","dan","dat","die","dit","een","en","er","had","heb","hem","het","hij","hoe","hun","ik","in","is","je","kan","me","men","met","mij","nog","nu","of","ons","ook","te","tot","uit","van","was","wat","we","wel","wij","zal","ze","zei","zij","zo","zou","aangaande","aangezien","achter","achterna","afgelopen","aldaar","aldus","alhoewel","alias","alle","allebei","alleen","alsnog","altijd","altoos","ander","andere","anders","anderszins","behalve","behoudens","beide","beiden","ben","beneden","bent","bepaald","betreffende","binnen","binnenin","boven","bovenal","bovendien","bovengenoemd","bovenstaand","bovenvermeld","buiten","daar","daarheen","daarin","daarna","daarnet","daarom","daarop","daarvanlangs","de","dikwijls","door","doorgaand","dus","echter","eer","eerdat","eerder","eerlang","eerst","elk","elke","enig","enigszins","enkel","erdoor","even","eveneens","evenwel","gauw","gedurende","geen","gehad","gekund","geleden","gelijk","gemoeten","gemogen","geweest","gewoon","gewoonweg","haar","hadden","hare","hebben","hebt","heeft","hen","hierbeneden","hierboven","hoewel","hunne","ikzelf","inmiddels","inzake","jezelf","jij","jijzelf","jou","jouw","jouwe","juist","jullie","klaar","kon","konden","krachtens","kunnen","kunt","later","liever","maar","mag","meer","mezelf","mijn","mijnent","mijner","mijzelf","misschien","mocht","mochten","moest","moesten","moet","moeten","mogen","na","naar","nadat","net","niet","noch","nogal","ofschoon","om","omdat","omhoog","omlaag","omstreeks","omtrent","omver","onder","ondertussen","ongeveer","onszelf","onze","op","opnieuw","opzij","over","overeind","overigens","pas","precies","reeds","rond","rondom","sedert","sinds","sindsdien","slechts","sommige","spoedig","steeds","tamelijk","tenzij","terwijl","thans","tijdens","toch","toen","toenmaals","toenmalig","totdat","tussen","uitgezonderd","vaakwat","vandaan","vanuit","vanwege","veeleer","verder","vervolgens","vol","volgens","voor","vooraf","vooral","vooralsnog","voorbij","voordat","voordezen","voordien","voorheen","voorop","vooruit","vrij","vroeg","waar","waarom","wanneer","want","waren","weer","weg","wegens","weldra","welk","welke","wie","wiens","wier","wijzelf","zelfs","zichzelf","zijn","zijne","zodra","zonder","zouden","zowat","zulke","zullen","zult","rt","ık","deze","u","via","-",",",'"[full_text": ','"truncated', '"rt',' '], inputCol='words_token', outputCol='words_clean')
data_clean = remover.transform(tokenized).select('Date', 'words_clean')
print('############ Data Cleaning extract:')
data_clean.show()

############ Data Cleaning extract:
+--------------------+--------------------+
|                Date|         words_clean|
+--------------------+--------------------+
|"Fri May 29 15:38...|["@sintsonja, @po...|
|"Fri May 29 15:38...|[@narkobars:, sho...|
|"Fri May 29 15:38...|["@kellyovercoron...|
|"Fri May 29 15:38...|["@tobientin, jaj...|
|"Fri May 29 15:38...|["@timm025, open,...|
|"Fri May 29 15:38...|["@nieuwsblad_be,...|
|"Fri May 29 15:38...|["@ozankemalozan,...|
|"Fri May 29 15:38...|["@sq__d, @torfsb...|
|"Fri May 29 15:38...|["\ud83c\udfac, m...|
|"Fri May 29 15:38...|["@ciciloqq, hy, ...|
|"Fri May 29 15:38...|["hercule, poirot...|
|"Fri May 29 15:38...|["@gbr8898, @matt...|
|"Fri May 29 15:38...|["@fransoldejans,...|
|"Fri May 29 15:38...|["@crypto4all9, @...|
|"Fri May 29 15:38...|["jungkook, wtf, ...|
|"Fri May 29 15:38...|[@studıodebalie:,...|
|"Fri May 29 15:38...|["like, w, htklem...|
|"Fri May 29 15:38...|["andre, rieu, am...|
|"Fri May 29 15:38...|["@advocaatboone,.

In [12]:
result = data_clean.withColumn('words_clean', f.explode(f.col('words_clean'))) \
  .groupBy('words_clean') \
  .count().sort('count', ascending=False) \

print('############')
result.show()

############
+-----------+-----+
|words_clean|count|
+-----------+-----+
|           |  850|
|       gaat|  237|
|     mensen|  222|
|      wordt|  200|
|       goed|  196|
|       echt|  188|
|       veel|  174|
|          1|  166|
|       eens|  162|
|       hier|  147|
|       gaan|  147|
|        wil|  139|
|       heel|  136|
|     worden|  134|
|       iets|  121|
|      tegen|  121|
|         ja|  120|
|       jaar|  120|
|     nieuwe|  118|
|         ın|  113|
+-----------+-----+
only showing top 20 rows



In [13]:
data_clean_test= data_clean

In [14]:
data_clean_test.show(truncate=False)


+-------------------------------------+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|Date                                 |words_clean                                                                                                                                                                                                               |
+-------------------------------------+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|"Fri May 29 15:38:51 +0000 2020", "id|["@sintsonja, @politiekdelftnl, @avalex_nieuws, @mar10ah, @zuidpoort, @jpdewit, @gjevalk, @koelewijnmarcel, melding, maak, buitenbeter, app, wordt, volgende, opgehaald",]              

In [15]:
tokenizerForDate = Tokenizer(inputCol="Date", outputCol="date_Token")


In [16]:
tokenizedForDate = tokenizerForDate.transform(data_clean_test).select('Date','words_clean','date_Token')

In [17]:
removerForDate = StopWordsRemover(stopWords=[',','id', '"id','"fri',"+0000",'2020",' ], inputCol='date_Token', outputCol='date_clean')


In [18]:
date_clean = removerForDate.transform(tokenizedForDate).select('words_clean', 'date_clean')

In [19]:
date_clean.show()

+--------------------+-------------------+
|         words_clean|         date_clean|
+--------------------+-------------------+
|["@sintsonja, @po...|[may, 29, 15:38:51]|
|[@narkobars:, sho...|[may, 29, 15:38:51]|
|["@kellyovercoron...|[may, 29, 15:38:50]|
|["@tobientin, jaj...|[may, 29, 15:38:48]|
|["@timm025, open,...|[may, 29, 15:38:48]|
|["@nieuwsblad_be,...|[may, 29, 15:38:47]|
|["@ozankemalozan,...|[may, 29, 15:38:45]|
|["@sq__d, @torfsb...|[may, 29, 15:38:45]|
|["\ud83c\udfac, m...|[may, 29, 15:38:44]|
|["@ciciloqq, hy, ...|[may, 29, 15:38:43]|
|["hercule, poirot...|[may, 29, 15:38:43]|
|["@gbr8898, @matt...|[may, 29, 15:38:41]|
|["@fransoldejans,...|[may, 29, 15:38:41]|
|["@crypto4all9, @...|[may, 29, 15:38:41]|
|["jungkook, wtf, ...|[may, 29, 15:38:40]|
|[@studıodebalie:,...|[may, 29, 15:38:39]|
|["like, w, htklem...|[may, 29, 15:38:39]|
|["andre, rieu, am...|[may, 29, 15:38:39]|
|["@advocaatboone,...|[may, 29, 15:38:38]|
|["@victoria_jaf, ...|[may, 29, 15:38:37]|
+----------

In [20]:
result3 = date_clean.withColumn('words_clean', f.explode(f.col('words_clean'))) \
  .groupBy('words_clean') \
  .count().sort('count', ascending=False) 

In [21]:
date_clean.show(10 ,truncate=False)

+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-------------------+
|words_clean                                                                                                                                                                                                               |date_clean         |
+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-------------------+
|["@sintsonja, @politiekdelftnl, @avalex_nieuws, @mar10ah, @zuidpoort, @jpdewit, @gjevalk, @koelewijnmarcel, melding, maak, buitenbeter, app, wordt, volgende, opgehaald",]                                                |[may, 29, 15:38:51]|
|[@narkobars:, shoegaze\n\nhttps://t

In [22]:
import datetime
def getDate(x):
    if x is not None:
        return str(datetime.strptime(x,'%b, %d, %H:%M:%S +0000').replace(tzinfo=pytz.UTC).strftime("%m-%d %H:%M:%S"))
    else:
        return None

In [23]:
date_clean.show()

+--------------------+-------------------+
|         words_clean|         date_clean|
+--------------------+-------------------+
|["@sintsonja, @po...|[may, 29, 15:38:51]|
|[@narkobars:, sho...|[may, 29, 15:38:51]|
|["@kellyovercoron...|[may, 29, 15:38:50]|
|["@tobientin, jaj...|[may, 29, 15:38:48]|
|["@timm025, open,...|[may, 29, 15:38:48]|
|["@nieuwsblad_be,...|[may, 29, 15:38:47]|
|["@ozankemalozan,...|[may, 29, 15:38:45]|
|["@sq__d, @torfsb...|[may, 29, 15:38:45]|
|["\ud83c\udfac, m...|[may, 29, 15:38:44]|
|["@ciciloqq, hy, ...|[may, 29, 15:38:43]|
|["hercule, poirot...|[may, 29, 15:38:43]|
|["@gbr8898, @matt...|[may, 29, 15:38:41]|
|["@fransoldejans,...|[may, 29, 15:38:41]|
|["@crypto4all9, @...|[may, 29, 15:38:41]|
|["jungkook, wtf, ...|[may, 29, 15:38:40]|
|[@studıodebalie:,...|[may, 29, 15:38:39]|
|["like, w, htklem...|[may, 29, 15:38:39]|
|["andre, rieu, am...|[may, 29, 15:38:39]|
|["@advocaatboone,...|[may, 29, 15:38:38]|
|["@victoria_jaf, ...|[may, 29, 15:38:37]|
+----------

In [24]:
date_clean.withColumn('date_clean', date_format(f.col("date_clean"),"mm, dd, dd").alias("yyyy MM dd"))

AnalysisException: cannot resolve 'date_format(date_clean, 'mm, dd, dd')' due to data type mismatch: argument 1 requires timestamp type, however, 'date_clean' is of array<string> type.;
'Project [words_clean#29, date_format(date_clean#94, mm, dd, dd, Some(Europe/Berlin)) AS date_clean#142]
+- Project [words_clean#29, date_clean#94]
   +- Project [Date#0, words_clean#29, date_Token#81, UDF(date_Token#81) AS date_clean#94]
      +- Project [Date#0, words_clean#29, date_Token#81]
         +- Project [Date#0, words_clean#29, UDF(Date#0) AS date_Token#81]
            +- Project [Date#0, words_clean#29]
               +- Project [Date#0, Text#1, words_token#16, UDF(words_token#16) AS words_clean#29]
                  +- Project [Date#0, Text#1, words_token#16]
                     +- Project [Date#0, Text#1, UDF(Text#1) AS words_token#16]
                        +- LogicalRDD [Date#0, Text#1], false


In [ ]:
date_format(current_timestamp(),"yyyy MM dd").alias("date_format")